In [18]:
!pip install PyPDF2

import re
import random
from collections import defaultdict
import PyPDF2

In [19]:
def cleaning(file):
  corpus = ""
  try:
    with open(file, "rb") as f:
      pdf_reader = PyPDF2.PdfReader(f)
      for page_num in range(len(pdf_reader.pages)):
        page = pdf_reader.pages[page_num]

        page_text = page.extract_text()
        if page_text:
          corpus += " " + page_text
  except Exception as e:
    print(f"Error reading PDF: {e}")
    return ""


  text = corpus
  start = re.search(r"\*\*\* START OF THIS PROJECT GUTENBERG EBOOK", text)
  end = re.search(r"\*\*\* END OF THIS PROJECT GUTENBERG EBOOK", text)

  if start and end:
    text = text[start.end():end.start()]


  text = text.lower()
  text = re.sub(r"[^a-z\s]", " ", text)
  text = re.sub(r"\s+", " ", text)

  return text.strip()


In [20]:
def model(tokens,n=5):
  m = defaultdict(list)

  for i in range(len(tokens)-n):
    context = tuple(tokens[i:i+n-1])
    target = tokens[i+n-1]
    m[context].append(target)

  return m

In [21]:
def generation(model,seedtext,n=5,length=30):
  seedtokens = seedtext.lower().split()
  output = seedtokens[:]

  for i in range(length):
    context = tuple(output[-(n-1):])
    if context not in model:
      break

    next = random.choice(model[context])
    output.append(next)

  return " ".join(output)

In [22]:
if __name__ == "__main__":
  file = "/content/sherlock_holmes.pdf"
  n=5
  text = cleaning(file)

  if not text:
    print("No text extracted")
  else:
    tokens = text.split()
    print(f"Total tokens: {len(tokens)}")
    model = model(tokens,n)
    print(f"Model: {model}")

    inputdata = [ "the day was very","it was evident that","i could not help"]

    for i,seed in enumerate(inputdata,1):
      print(f"\nSample {i}")
      print("Input:",seed)
      op = generation(model,seed,n=n,length=30)
      print("Output:",op)

Total tokens: 107439
Model: defaultdict(<class 'list'>, {('the', 'adventures', 'of', 'sherlock'): ['holmes'], ('adventures', 'of', 'sherlock', 'holmes'): ['arthur'], ('of', 'sherlock', 'holmes', 'arthur'): ['conan'], ('sherlock', 'holmes', 'arthur', 'conan'): ['doyle'], ('holmes', 'arthur', 'conan', 'doyle'): ['this'], ('arthur', 'conan', 'doyle', 'this'): ['text'], ('conan', 'doyle', 'this', 'text'): ['is'], ('doyle', 'this', 'text', 'is'): ['provided'], ('this', 'text', 'is', 'provided'): ['to'], ('text', 'is', 'provided', 'to'): ['you'], ('is', 'provided', 'to', 'you'): ['as'], ('provided', 'to', 'you', 'as'): ['is'], ('to', 'you', 'as', 'is'): ['without'], ('you', 'as', 'is', 'without'): ['any'], ('as', 'is', 'without', 'any'): ['warranty'], ('is', 'without', 'any', 'warranty'): ['no'], ('without', 'any', 'warranty', 'no'): ['warranties'], ('any', 'warranty', 'no', 'warranties'): ['of'], ('warranty', 'no', 'warranties', 'of'): ['any'], ('no', 'warranties', 'of', 'any'): ['kind'], (